## About Dataset
Context
This is a small subset of dataset of Book reviews from Amazon Kindle Store category.

Content
5-core dataset of product reviews from Amazon Kindle Store category from May 1996 - July 2014. Contains total of 982619 entries. Each reviewer has at least 5 reviews and each product has at least 5 reviews in this dataset.
Columns

- asin - ID of the product, like B000FA64PK
- helpful - helpfulness rating of the review - example: 2/3.
- overall - rating of the product.
- reviewText - text of the review (heading).
- reviewTime - time of the review (raw).
- reviewerID - ID of the reviewer, like A3SPTOKDG7WBLN
- reviewerName - name of the reviewer.
- summary - summary of the review (description).
- unixReviewTime - unix timestamp.

Acknowledgements
This dataset is taken from Amazon product data, Julian McAuley, UCSD website. http://jmcauley.ucsd.edu/data/amazon/

License to the data files belong to them.

Inspiration
- Sentiment analysis on reviews.
- Understanding how people rate usefulness of a review/ What factors influence helpfulness of a review.
- Fake reviews/ outliers.
- Best rated product IDs, or similarity between products based on reviews alone (not the best idea ikr).
- Any other interesting analysis

#### Best Practises
1. Preprocessing And Cleaning
2. Train Test Split
3. BOW,TFIDF,Word2vec
4. Train ML algorithms

In [1]:
## Load the dataset
import pandas as pd
data = pd.read_csv('all_kindle_review.csv')

In [2]:
data.head()

Unnamed: 0.1  Unnamed: 0        asin  helpful  rating  \
0             0       11539  B0033UV8HI  [8, 10]       3   
1             1        5957  B002HJV4DE   [1, 1]       5   
2             2        9146  B002ZG96I4   [0, 0]       3   
3             3        7038  B002QHWOEU   [1, 3]       3   
4             4        1776  B001A06VJ8   [0, 1]       4   

                                          reviewText   reviewTime  \
0  Jace Rankin may be short, but he's nothing to ...   09 2, 2010   
1  Great short read.  I didn't want to put it dow...   10 8, 2013   
2  I'll start by saying this is the first of four...  04 11, 2014   
3  Aggie is Angela Lansbury who carries pocketboo...   07 5, 2014   
4  I did not expect this type of book to be in li...  12 31, 2012   

       reviewerID  reviewerName                   summary  unixReviewTime  
0  A3HHXRELK8BHQG        Ridley  Entertaining But Average      1283385600  
1  A2RGNZ0TRF578I  Holly Butler   Terrific menage scenes!      1381190400  
2  A3S0H2HV6U1I7F       Merissa          Snapdragon Alley      1397174400  
3   AC4OQW3GZ919J    Cleargrace    very light murder cozy      1404518400  
4  A3C9V987IQHOQD      Rjostler                      Book      1356912000

In [3]:
data = data[['reviewText','rating']]

In [4]:
data.shape

(12000, 2)

In [5]:
# Missing values
data.isnull().sum()

reviewText    0
rating        0
dtype: int64

In [6]:
data.rating.unique()

array([3, 5, 4, 2, 1], dtype=int64)

In [7]:
data['rating'].value_counts()

5    3000
4    3000
3    2000
2    2000
1    2000
Name: rating, dtype: int64

# Pre-processing and Cleaning

In [8]:
## postive review is 1 and negative review is 0
data['rating'] = data['rating'].apply(lambda x:0 if x<3 else 1)

In [9]:
## Lowercasing
data['reviewText'] = data['reviewText'].str.lower()

In [10]:
import re
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
from bs4 import BeautifulSoup

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\monik\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [11]:
## Removing special characters
data['reviewText']=data['reviewText'].apply(lambda x:re.sub('[^a-z A-z 0-9-]+', '',x))
## Remove the stopswords
data['reviewText']=data['reviewText'].apply(lambda x:" ".join([y for y in x.split() if y not in stopwords.words('english')]))
## Remove url 
data['reviewText']=data['reviewText'].apply(lambda x: re.sub(r'(http|https|ftp|ssh)://([\w_-]+(?:(?:\.[\w_-]+)+))([\w.,@?^=%&:/~+#-]*[\w@?^=%&/~+#-])?', '' , str(x)))
## Remove html tags
data['reviewText']=data['reviewText'].apply(lambda x: BeautifulSoup(x, 'lxml').get_text())
## Remove any additional spaces
data['reviewText']=data['reviewText'].apply(lambda x: " ".join(x.split()))

C:\Users\monik\AppData\Local\Temp\ipykernel_11548\727113573.py:8: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  data['reviewText']=data['reviewText'].apply(lambda x: BeautifulSoup(x, 'lxml').get_text())


In [12]:
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()

In [13]:
def lemmatize_words(text):
    return " ".join([lemmatizer.lemmatize(word) for word in text.split()])

In [14]:
data['reviewText']=data['reviewText'].apply(lambda x:lemmatize_words(x))

In [15]:
## Train Test Split
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test = train_test_split(data['reviewText'],data['rating'],test_size=0.20)

In [16]:
train_corpus=[]
for i in range(len(x_train)):
    review = x_train.iloc[i]
    review = ' '.join(review.split())
    train_corpus.append(review)
test_corpus=[]
for i in range(len(x_test)):
    review = x_test.iloc[i]
    review = ' '.join(review.split())
    test_corpus.append(review)

In [17]:
train_corpus

['story started okay turn page thought downloaded ending jeff get car leaf ending',
 'child saw latest movie based jules verne book decided let read original story move little slowly normal time-frame writing style funny idea natural science storyline good adventure',
 'sorry brought product wanted thought would sent back lost paper work',
 'didnt read started another planet isnt kind reading like real read',
 'damn good read book definitely page turner author made wide come alive must read',
 'john carter one first introduction reading sci-fi enjoyed book young man re-read disney movie came yes movie train wreck book worth read dont base reading book movie recommend series book younger reader',
 'cannot believe paid story started fine 15 minute later story way ended dumbit fup waste minute life',
 'weaving fact fiction supernatural bent appears author specialty well ive always intrigued salem witch trial book offer totally new idea may motivated perpetrator horrific shameful time hist

In [18]:
test_corpus

['purchased along kindle dx cover 1000it sturdy little heavy needsalso got concerned way attache kindle make break kindle one dayso purchased icover model red safe side',
 'took 10 minute read paid prelude best sure review friend',
 'love one author great job giving substance character loved viewpoint hero heroine laugh loud funny many place well worth money',
 'reviewagain favorite tropefriends lover omg one done well really really loved book book description really well-done going add anything setup story get right review part reviewi love way two character written realistically yes absolutely best friend thing heat sexually everything becomes really awkward tense mitch kerri sudden fighting constantly sniping everything thats one thing work really good friendsthey may omg know push others button tookelly wrote really wellyou see sexual chemistry two sizzling using aggression fight aggression becomes much give sexual tensionomg incredibly hot think honestly say sexual scene book abso

In [19]:
from nltk import sent_tokenize
from gensim.utils import simple_preprocess

In [20]:
train_words = []
for sent in train_corpus:
    sent_token = sent_tokenize(sent)
    for word in sent_token:
        train_words.append(simple_preprocess(word))
test_words = []
for sent in test_corpus:
    sent_token = sent_tokenize(sent)
    for word in sent_token:
        test_words.append(simple_preprocess(word))

In [21]:
train_words

[['story',
  'started',
  'okay',
  'turn',
  'page',
  'thought',
  'downloaded',
  'ending',
  'jeff',
  'get',
  'car',
  'leaf',
  'ending'],
 ['child',
  'saw',
  'latest',
  'movie',
  'based',
  'jules',
  'verne',
  'book',
  'decided',
  'let',
  'read',
  'original',
  'story',
  'move',
  'little',
  'slowly',
  'normal',
  'time',
  'frame',
  'writing',
  'style',
  'funny',
  'idea',
  'natural',
  'science',
  'storyline',
  'good',
  'adventure'],
 ['sorry',
  'brought',
  'product',
  'wanted',
  'thought',
  'would',
  'sent',
  'back',
  'lost',
  'paper',
  'work'],
 ['didnt',
  'read',
  'started',
  'another',
  'planet',
  'isnt',
  'kind',
  'reading',
  'like',
  'real',
  'read'],
 ['damn',
  'good',
  'read',
  'book',
  'definitely',
  'page',
  'turner',
  'author',
  'made',
  'wide',
  'come',
  'alive',
  'must',
  'read'],
 ['john',
  'carter',
  'one',
  'first',
  'introduction',
  'reading',
  'sci',
  'fi',
  'enjoyed',
  'book',
  'young',
  'man',

In [22]:
test_words

[['purchased',
  'along',
  'kindle',
  'dx',
  'cover',
  'it',
  'sturdy',
  'little',
  'heavy',
  'needsalso',
  'got',
  'concerned',
  'way',
  'attache',
  'kindle',
  'make',
  'break',
  'kindle',
  'one',
  'dayso',
  'purchased',
  'icover',
  'model',
  'red',
  'safe',
  'side'],
 ['took',
  'minute',
  'read',
  'paid',
  'prelude',
  'best',
  'sure',
  'review',
  'friend'],
 ['love',
  'one',
  'author',
  'great',
  'job',
  'giving',
  'substance',
  'character',
  'loved',
  'viewpoint',
  'hero',
  'heroine',
  'laugh',
  'loud',
  'funny',
  'many',
  'place',
  'well',
  'worth',
  'money'],
 ['reviewagain',
  'favorite',
  'tropefriends',
  'lover',
  'omg',
  'one',
  'done',
  'well',
  'really',
  'really',
  'loved',
  'book',
  'book',
  'description',
  'really',
  'well',
  'done',
  'going',
  'add',
  'anything',
  'setup',
  'story',
  'get',
  'right',
  'review',
  'part',
  'reviewi',
  'love',
  'way',
  'two',
  'character',
  'written',
  'realis

In [23]:
import gensim
## Training Word2Vec from scratch using gensim
train_model = gensim.models.Word2Vec(train_words)

In [24]:
## To get all the Vocabulary
train_model.wv.index_to_key

['book',
 'story',
 'read',
 'one',
 'character',
 'like',
 'good',
 'would',
 'really',
 'love',
 'get',
 'time',
 'author',
 'reading',
 'well',
 'first',
 'series',
 'much',
 'even',
 'didnt',
 'short',
 'know',
 'way',
 'great',
 'could',
 'make',
 'little',
 'sex',
 'dont',
 'want',
 'two',
 'thing',
 'think',
 'plot',
 'find',
 'romance',
 'also',
 'im',
 'life',
 'end',
 'see',
 'enjoyed',
 'scene',
 'go',
 'written',
 'never',
 'woman',
 'take',
 'lot',
 'many',
 'say',
 'year',
 'bit',
 'thought',
 'kindle',
 'work',
 'going',
 'give',
 'found',
 'interesting',
 'novel',
 'liked',
 'writing',
 'feel',
 'got',
 'loved',
 'hot',
 'another',
 'still',
 'though',
 'man',
 'star',
 'people',
 'enough',
 'better',
 'back',
 'come',
 'part',
 'friend',
 'review',
 'something',
 'made',
 'reader',
 'free',
 'page',
 'cant',
 'world',
 'need',
 'new',
 'wasnt',
 'doesnt',
 'keep',
 'bad',
 'relationship',
 'recommend',
 'enjoy',
 'next',
 'together',
 'start',
 'felt',
 'best',
 'put',

In [25]:
import numpy as np
from tqdm import tqdm

In [26]:
def avg_word2vec(doc):
    # remove out-of-vocabulary words
    #sent = [word for word in doc if word in model.wv.index_to_key]
    #print(sent)
    
    return np.mean([train_model.wv[word] for word in doc if word in train_model.wv.index_to_key],axis=0)
                #or [np.zeros(len(model.wv.index_to_key))], axis=0)

In [27]:
#apply for the entire sentences
x_train_new=[]
for i in tqdm(range(len(train_words))):
    x_train_new.append(avg_word2vec(train_words[i]))
x_test_new=[]
for i in tqdm(range(len(test_words))):
    x_test_new.append(avg_word2vec(test_words[i]))


100%|██████████| 2400/2400 [00:05<00:00, 418.84it/s]


In [28]:
x_train_new

[array([-0.21739307,  0.45748556, -0.21240851,  0.06602324,  0.04221221,
        -0.8139312 ,  0.34988266,  0.80315346, -0.38668746, -0.23213604,
         0.03578905, -0.47164732,  0.00665182,  0.1959018 ,  0.342343  ,
        -0.3483643 ,  0.32727417, -0.41488424, -0.2633989 , -0.7271099 ,
         0.22488499, -0.03865236,  0.5400257 , -0.12105553, -0.13035527,
         0.02557147, -0.25410536,  0.02845598, -0.35436806,  0.0055503 ,
         0.2916362 , -0.14279614,  0.07456377, -0.5474052 , -0.32260785,
         0.3846024 ,  0.09716062, -0.17319338, -0.06449064, -0.49665847,
         0.21686047, -0.695785  , -0.44983965, -0.0289658 ,  0.30137503,
        -0.4330309 , -0.30004045, -0.15289785,  0.4525406 ,  0.4132621 ,
         0.01517842, -0.32509723, -0.0391283 ,  0.08014142, -0.11981004,
         0.29341367,  0.2144663 , -0.2547166 ,  0.02293101,  0.44997314,
         0.23163968, -0.06720518,  0.2875961 , -0.02044429, -0.51531893,
         0.7385367 ,  0.26111245,  0.49508005, -0.7

In [29]:
x_test_new

[array([-0.13428989,  0.13813645, -0.03690331,  0.10672797, -0.01655333,
        -0.6222843 ,  0.05577804,  0.8976188 , -0.19919711, -0.06248131,
        -0.28773093, -0.5427649 , -0.09708565,  0.07719081,  0.05738383,
        -0.184969  ,  0.17842314, -0.20509057, -0.12498134, -0.54046756,
         0.25773492,  0.09360661,  0.1709328 , -0.36809763, -0.06602176,
        -0.09967998, -0.11634192, -0.05461005, -0.40637842, -0.08111664,
         0.1512379 ,  0.03348991,  0.15449063, -0.40775672, -0.20432036,
         0.39044166,  0.08988261, -0.43478057, -0.34095255, -0.66923934,
         0.04121544, -0.40635592, -0.13216665,  0.0221108 ,  0.483824  ,
        -0.23517969, -0.30825144, -0.23811738,  0.31282786,  0.23377565,
         0.2920441 , -0.49055707, -0.1616506 , -0.04623624, -0.45647144,
         0.13007596,  0.06027672, -0.21155795, -0.22816056,  0.24682601,
         0.1110669 ,  0.26866424, -0.07776228,  0.05646268, -0.2997897 ,
         0.5047806 ,  0.03379943,  0.3700277 , -0.3

In [30]:
from sklearn.naive_bayes import GaussianNB
nb_model=GaussianNB().fit(x_train_new,y_train)


In [31]:
from sklearn.metrics import confusion_matrix,accuracy_score,classification_report

In [32]:
y_pred = nb_model.predict(x_test_new)

In [33]:
confusion_matrix(y_test,y_pred)

array([[ 543,  237],
       [ 506, 1114]], dtype=int64)

In [34]:
print("Accuracy with Word2Vec: ",accuracy_score(y_test,y_pred))

Accuracy with Word2Vec:  0.6904166666666667


In [35]:
print("Accuracy with Word2Vec after cross validation and hyperparameter tuning: ",accuracy_score(y_test,y_pred))

Accuracy with Word2Vec after cross validation and hyperparameter tuning:  0.6904166666666667


## Trying this with Random Forest Classifier

In [36]:
from sklearn.ensemble import RandomForestClassifier
model = RandomForestClassifier(n_estimators=100, random_state=42)

In [37]:
# Train the model
model.fit(x_train_new, y_train)

# Make predictions
predictions = model.predict(x_test_new)

In [38]:
# Evaluate the model
accuracy = accuracy_score(y_test, predictions)
report = classification_report(y_test, predictions)

print(f"Accuracy: {accuracy:.2f}")
print("Classification Report:")
print(report)

Accuracy: 0.77
Classification Report:
              precision    recall  f1-score   support

           0       0.67      0.55      0.61       780
           1       0.80      0.87      0.83      1620

    accuracy                           0.77      2400
   macro avg       0.74      0.71      0.72      2400
weighted avg       0.76      0.77      0.76      2400

